# Lab 8: Propositional and Predicate Logic with Resolution

This notebook demonstrates:
1. Propositional Logic with Resolution
2. First-Order Predicate Logic (FOPL) with Resolution
3. Solutions to three FOPL problems using resolution algorithm


# Propositional Logic Example


In [9]:
import itertools
from typing import List, Set, Dict, Tuple, Optional
import re

class PropositionalClause:
    """Represents a clause in propositional logic (disjunction of literals)"""
    
    def __init__(self, literals: List[str]):
        self.literals = set(literals)
    
    def __str__(self):
        if not self.literals:
            return "□"  # Empty clause (contradiction)
        return " ∨ ".join(sorted(self.literals))
    
    def __eq__(self, other):
        return self.literals == other.literals
    
    def __hash__(self):
        return hash(frozenset(self.literals))
    
    def is_empty(self):
        return len(self.literals) == 0
    
    def resolve_with(self, other):
        """Resolve this clause with another clause"""
        new_literals = set()
        resolved = False
        
        for lit1 in self.literals:
            for lit2 in other.literals:
                # Check if literals are complementary
                if lit1.startswith('¬') and lit2 == lit1[1:]:
                    # Resolve ¬P and P
                    new_literals = (self.literals - {lit1}) | (other.literals - {lit2})
                    resolved = True
                    break
                elif lit2.startswith('¬') and lit1 == lit2[1:]:
                    # Resolve P and ¬P
                    new_literals = (self.literals - {lit1}) | (other.literals - {lit2})
                    resolved = True
                    break
            if resolved:
                break
        
        if resolved:
            return PropositionalClause(list(new_literals))
        return None

def propositional_resolution(clauses: List[PropositionalClause]) -> Tuple[bool, List[str]]:
    """Apply resolution algorithm to propositional clauses"""
    clauses_set = set(clauses)
    new_clauses = set()
    steps = []
    
    steps.append("Initial clauses:")
    for i, clause in enumerate(clauses):
        steps.append(f"  {i+1}. {clause}")
    
    iteration = 1
    while True:
        steps.append(f"\nIteration {iteration}:")
        iteration_new = set()
        
        # Try to resolve each pair of clauses
        clause_list = list(clauses_set)
        for i in range(len(clause_list)):
            for j in range(i + 1, len(clause_list)):
                resolvent = clause_list[i].resolve_with(clause_list[j])
                if resolvent is not None:
                    steps.append(f"  Resolving '{clause_list[i]}' and '{clause_list[j]}' → '{resolvent}'")
                    
                    if resolvent.is_empty():
                        steps.append("  ✓ Empty clause derived! Contradiction found.")
                        return True, steps
                    
                    iteration_new.add(resolvent)
        
        # Check if no new clauses were generated
        if iteration_new.issubset(clauses_set):
            steps.append("  No new clauses generated. Resolution terminates.")
            return False, steps
        
        new_clauses.update(iteration_new)
        clauses_set.update(iteration_new)
        iteration += 1

# Example: Propositional Logic Resolution
print("=== Propositional Logic Example ===")
print("Knowledge Base:")
print("1. If it rains, then the ground is wet: R → W")
print("2. If the ground is wet, then it's slippery: W → S")
print("3. It rains: R")
print("Query: Is it slippery? S")
print()

# Convert to CNF and add negation of query
print("Converting to CNF:")
print("1. R → W ≡ ¬R ∨ W")
print("2. W → S ≡ ¬W ∨ S")
print("3. R")
print("4. ¬S (negation of query)")
print()

# Create clauses
clauses = [
    PropositionalClause(['¬R', 'W']),  # R → W
    PropositionalClause(['¬W', 'S']),  # W → S
    PropositionalClause(['R']),        # R
    PropositionalClause(['¬S'])        # ¬S (negation of query)
]

# Apply resolution
result, steps = propositional_resolution(clauses)

print("Resolution Process:")
for step in steps:
    print(step)

print(f"\nConclusion: {'Query is PROVABLE' if result else 'Query is NOT provable'}")

=== Propositional Logic Example ===
Knowledge Base:
1. If it rains, then the ground is wet: R → W
2. If the ground is wet, then it's slippery: W → S
3. It rains: R
Query: Is it slippery? S

Converting to CNF:
1. R → W ≡ ¬R ∨ W
2. W → S ≡ ¬W ∨ S
3. R
4. ¬S (negation of query)

Resolution Process:
Initial clauses:
  1. W ∨ ¬R
  2. S ∨ ¬W
  3. R
  4. ¬S

Iteration 1:
  Resolving 'R' and 'W ∨ ¬R' → 'W'
  Resolving '¬S' and 'S ∨ ¬W' → '¬W'
  Resolving 'S ∨ ¬W' and 'W ∨ ¬R' → 'S ∨ ¬R'

Iteration 2:
  Resolving 'R' and 'W ∨ ¬R' → 'W'
  Resolving 'R' and 'S ∨ ¬R' → 'S'
  Resolving '¬S' and 'S ∨ ¬R' → '¬R'
  Resolving '¬S' and 'S ∨ ¬W' → '¬W'
  Resolving 'W' and '¬W' → '□'
  ✓ Empty clause derived! Contradiction found.

Conclusion: Query is PROVABLE


# First-Order Predicate Logic Framework

Now let's implement a framework for First-Order Predicate Logic with unification and resolution.

In [10]:
import re
from typing import Dict, List, Optional, Set, Tuple, Union

class Term:
    """Represents a term in first-order logic"""
    pass

class Variable(Term):
    def __init__(self, name: str):
        self.name = name
    
    def __str__(self):
        return self.name
    
    def __eq__(self, other):
        return isinstance(other, Variable) and self.name == other.name
    
    def __hash__(self):
        return hash(('var', self.name))

class Constant(Term):
    def __init__(self, name: str):
        self.name = name
    
    def __str__(self):
        return self.name
    
    def __eq__(self, other):
        return isinstance(other, Constant) and self.name == other.name
    
    def __hash__(self):
        return hash(('const', self.name))

class Function(Term):
    def __init__(self, name: str, args: List[Term]):
        self.name = name
        self.args = args
    
    def __str__(self):
        if not self.args:
            return self.name
        return f"{self.name}({', '.join(str(arg) for arg in self.args)})"
    
    def __eq__(self, other):
        return (isinstance(other, Function) and 
                self.name == other.name and 
                self.args == other.args)
    
    def __hash__(self):
        return hash(('func', self.name, tuple(self.args)))

class Predicate:
    def __init__(self, name: str, args: List[Term], negated: bool = False):
        self.name = name
        self.args = args
        self.negated = negated
    
    def __str__(self):
        pred_str = f"{self.name}({', '.join(str(arg) for arg in self.args)})"
        return f"¬{pred_str}" if self.negated else pred_str
    
    def __eq__(self, other):
        return (isinstance(other, Predicate) and 
                self.name == other.name and 
                self.args == other.args and 
                self.negated == other.negated)
    
    def __hash__(self):
        return hash(('pred', self.name, tuple(self.args), self.negated))
    
    def negate(self):
        return Predicate(self.name, self.args, not self.negated)

class FOLClause:
    """Represents a clause in first-order logic"""
    
    def __init__(self, predicates: List[Predicate]):
        self.predicates = predicates
    
    def __str__(self):
        if not self.predicates:
            return "□"  # Empty clause
        return " ∨ ".join(str(pred) for pred in self.predicates)
    
    def __eq__(self, other):
        return isinstance(other, FOLClause) and set(self.predicates) == set(other.predicates)
    
    def __hash__(self):
        return hash(frozenset(self.predicates))
    
    def is_empty(self):
        return len(self.predicates) == 0
    
    def get_variables(self) -> Set[Variable]:
        variables = set()
        for pred in self.predicates:
            for arg in pred.args:
                if isinstance(arg, Variable):
                    variables.add(arg)
        return variables

def substitute(term: Term, substitution: Dict[Variable, Term]) -> Term:
    """Apply substitution to a term"""
    if isinstance(term, Variable):
        return substitution.get(term, term)
    elif isinstance(term, Constant):
        return term
    elif isinstance(term, Function):
        new_args = [substitute(arg, substitution) for arg in term.args]
        return Function(term.name, new_args)
    return term

def substitute_predicate(pred: Predicate, substitution: Dict[Variable, Term]) -> Predicate:
    """Apply substitution to a predicate"""
    new_args = [substitute(arg, substitution) for arg in pred.args]
    return Predicate(pred.name, new_args, pred.negated)

def substitute_clause(clause: FOLClause, substitution: Dict[Variable, Term]) -> FOLClause:
    """Apply substitution to a clause"""
    new_predicates = [substitute_predicate(pred, substitution) for pred in clause.predicates]
    return FOLClause(new_predicates)

def occurs_check(var: Variable, term: Term) -> bool:
    """Check if variable occurs in term (prevents infinite structures)"""
    if isinstance(term, Variable):
        return var == term
    elif isinstance(term, Function):
        return any(occurs_check(var, arg) for arg in term.args)
    return False

def unify_terms(term1: Term, term2: Term, substitution: Optional[Dict[Variable, Term]] = None) -> Optional[Dict[Variable, Term]]:
    """Unify two terms"""
    if substitution is None:
        substitution = {}
    
    # Apply current substitution
    term1 = substitute(term1, substitution)
    term2 = substitute(term2, substitution)
    
    if term1 == term2:
        return substitution
    
    if isinstance(term1, Variable):
        if occurs_check(term1, term2):
            return None
        substitution[term1] = term2
        return substitution
    
    if isinstance(term2, Variable):
        if occurs_check(term2, term1):
            return None
        substitution[term2] = term1
        return substitution
    
    if isinstance(term1, Function) and isinstance(term2, Function):
        if term1.name != term2.name or len(term1.args) != len(term2.args):
            return None
        
        for arg1, arg2 in zip(term1.args, term2.args):
            substitution = unify_terms(arg1, arg2, substitution)
            if substitution is None:
                return None
        return substitution
    
    return None

def unify_predicates(pred1: Predicate, pred2: Predicate) -> Optional[Dict[Variable, Term]]:
    """Unify two predicates if they are complementary"""
    if pred1.name != pred2.name or len(pred1.args) != len(pred2.args):
        return None
    
    if pred1.negated == pred2.negated:
        return None  # Not complementary
    
    substitution = {}
    for arg1, arg2 in zip(pred1.args, pred2.args):
        substitution = unify_terms(arg1, arg2, substitution)
        if substitution is None:
            return None
    
    return substitution

def rename_variables(clause: FOLClause, suffix: str) -> FOLClause:
    """Rename variables in clause to avoid conflicts"""
    var_mapping = {}
    
    def rename_term(term: Term) -> Term:
        if isinstance(term, Variable):
            if term not in var_mapping:
                var_mapping[term] = Variable(term.name + suffix)
            return var_mapping[term]
        elif isinstance(term, Function):
            new_args = [rename_term(arg) for arg in term.args]
            return Function(term.name, new_args)
        return term
    
    new_predicates = []
    for pred in clause.predicates:
        new_args = [rename_term(arg) for arg in pred.args]
        new_predicates.append(Predicate(pred.name, new_args, pred.negated))
    
    return FOLClause(new_predicates)

def resolve_clauses(clause1: FOLClause, clause2: FOLClause) -> List[FOLClause]:
    """Resolve two clauses using unification"""
    # Rename variables to avoid conflicts
    clause1_renamed = rename_variables(clause1, "1")
    clause2_renamed = rename_variables(clause2, "2")
    
    resolvents = []
    
    for i, pred1 in enumerate(clause1_renamed.predicates):
        for j, pred2 in enumerate(clause2_renamed.predicates):
            substitution = unify_predicates(pred1, pred2)
            if substitution is not None:
                # Create resolvent by removing unified predicates
                new_predicates = []
                
                # Add remaining predicates from clause1
                for k, pred in enumerate(clause1_renamed.predicates):
                    if k != i:
                        new_predicates.append(substitute_predicate(pred, substitution))
                
                # Add remaining predicates from clause2
                for k, pred in enumerate(clause2_renamed.predicates):
                    if k != j:
                        new_predicates.append(substitute_predicate(pred, substitution))
                
                resolvent = FOLClause(new_predicates)
                resolvents.append(resolvent)
    
    return resolvents

def fol_resolution(clauses: List[FOLClause]) -> Tuple[bool, List[str]]:
    """Apply resolution algorithm to first-order logic clauses"""
    clauses_set = set(clauses)
    steps = []
    
    steps.append("Initial clauses:")
    for i, clause in enumerate(clauses):
        steps.append(f"  {i+1}. {clause}")
    
    iteration = 1
    while True:
        steps.append(f"\nIteration {iteration}:")
        new_clauses = set()
        
        clause_list = list(clauses_set)
        for i in range(len(clause_list)):
            for j in range(i + 1, len(clause_list)):
                resolvents = resolve_clauses(clause_list[i], clause_list[j])
                for resolvent in resolvents:
                    steps.append(f"  Resolving '{clause_list[i]}' and '{clause_list[j]}' → '{resolvent}'")
                    
                    if resolvent.is_empty():
                        steps.append("  ✓ Empty clause derived! Contradiction found.")
                        return True, steps
                    
                    new_clauses.add(resolvent)
        
        if new_clauses.issubset(clauses_set) or not new_clauses:
            steps.append("  No new clauses generated. Resolution terminates.")
            return False, steps
        
        clauses_set.update(new_clauses)
        iteration += 1
        
        if iteration > 10:  # Prevent infinite loops
            steps.append("  Maximum iterations reached.")
            break
    
    return False, steps

print("First-Order Logic framework implemented successfully!")

First-Order Logic framework implemented successfully!


# Question 1: Traffic and Drivers

**Problem**: 
- Every traffic chases driver
- Every driver who horns is smart
- No traffic catches any smart driver
- Any traffic who chases some driver but does not catch him is frustrated

**Goal**: Prove "If all drivers horn, then all traffics are frustrated"

In [11]:
print("=== Question 1: Traffic and Drivers ===")
print()
print("Given facts:")
print("1. Every traffic chases driver")
print("2. Every driver who horns is smart")
print("3. No traffic catches any smart driver")
print("4. Any traffic who chases some driver but does not catch him is frustrated")
print()
print("Goal: If all drivers horn, then all traffics are frustrated")
print()

# Convert to FOPL
print("Converting to First-Order Predicate Logic:")
print("Predicates:")
print("  Traffic(x) - x is a traffic")
print("  Driver(x) - x is a driver")
print("  Chases(x,y) - x chases y")
print("  Horns(x) - x horns")
print("  Smart(x) - x is smart")
print("  Catches(x,y) - x catches y")
print("  Frustrated(x) - x is frustrated")
print()

print("FOPL statements:")
print("1. ∀x∀y (Traffic(x) ∧ Driver(y) → Chases(x,y))")
print("2. ∀x (Driver(x) ∧ Horns(x) → Smart(x))")
print("3. ∀x∀y (Traffic(x) ∧ Smart(y) → ¬Catches(x,y))")
print("4. ∀x∀y (Traffic(x) ∧ Driver(y) ∧ Chases(x,y) ∧ ¬Catches(x,y) → Frustrated(x))")
print()

print("Converting to CNF:")
print("1. ¬Traffic(x) ∨ ¬Driver(y) ∨ Chases(x,y)")
print("2. ¬Driver(x) ∨ ¬Horns(x) ∨ Smart(x)")
print("3. ¬Traffic(x) ∨ ¬Smart(y) ∨ ¬Catches(x,y)")
print("4. ¬Traffic(x) ∨ ¬Driver(y) ∨ ¬Chases(x,y) ∨ Catches(x,y) ∨ Frustrated(x)")
print()

# Create the clauses
x, y = Variable('x'), Variable('y')
traffic_x = Predicate('Traffic', [x])
driver_y = Predicate('Driver', [y])
driver_x = Predicate('Driver', [x])
chases_xy = Predicate('Chases', [x, y])
horns_x = Predicate('Horns', [x])
smart_x = Predicate('Smart', [x])
smart_y = Predicate('Smart', [y])
catches_xy = Predicate('Catches', [x, y])
frustrated_x = Predicate('Frustrated', [x])

clauses = [
    # 1. ¬Traffic(x) ∨ ¬Driver(y) ∨ Chases(x,y)
    FOLClause([traffic_x.negate(), driver_y.negate(), chases_xy]),
    
    # 2. ¬Driver(x) ∨ ¬Horns(x) ∨ Smart(x)
    FOLClause([driver_x.negate(), horns_x.negate(), smart_x]),
    
    # 3. ¬Traffic(x) ∨ ¬Smart(y) ∨ ¬Catches(x,y)
    FOLClause([traffic_x.negate(), smart_y.negate(), catches_xy.negate()]),
    
    # 4. ¬Traffic(x) ∨ ¬Driver(y) ∨ ¬Chases(x,y) ∨ Catches(x,y) ∨ Frustrated(x)
    FOLClause([traffic_x.negate(), driver_y.negate(), chases_xy.negate(), catches_xy, frustrated_x]),
]

# Add assumption: All drivers horn (∀x (Driver(x) → Horns(x)))
# CNF: ¬Driver(x) ∨ Horns(x)
clauses.append(FOLClause([driver_x.negate(), horns_x]))

# Add negation of conclusion: ∃x (Traffic(x) ∧ ¬Frustrated(x))
# CNF: Traffic(a) and ¬Frustrated(a) for some constant a
a = Constant('a')
clauses.append(FOLClause([Predicate('Traffic', [a])]))
clauses.append(FOLClause([Predicate('Frustrated', [a]).negate()]))

print("Knowledge base with assumptions and negated conclusion:")
for i, clause in enumerate(clauses):
    print(f"  {i+1}. {clause}")
print()

# Apply resolution
result, steps = fol_resolution(clauses)

print("Resolution Process:")
for step in steps:
    print(step)

print(f"\n✓ Conclusion: The statement is {'PROVABLE' if result else 'NOT provable'}")
if result:
    print("Therefore: If all drivers horn, then all traffics are frustrated.")

=== Question 1: Traffic and Drivers ===

Given facts:
1. Every traffic chases driver
2. Every driver who horns is smart
3. No traffic catches any smart driver
4. Any traffic who chases some driver but does not catch him is frustrated

Goal: If all drivers horn, then all traffics are frustrated

Converting to First-Order Predicate Logic:
Predicates:
  Traffic(x) - x is a traffic
  Driver(x) - x is a driver
  Chases(x,y) - x chases y
  Horns(x) - x horns
  Smart(x) - x is smart
  Catches(x,y) - x catches y
  Frustrated(x) - x is frustrated

FOPL statements:
1. ∀x∀y (Traffic(x) ∧ Driver(y) → Chases(x,y))
2. ∀x (Driver(x) ∧ Horns(x) → Smart(x))
3. ∀x∀y (Traffic(x) ∧ Smart(y) → ¬Catches(x,y))
4. ∀x∀y (Traffic(x) ∧ Driver(y) ∧ Chases(x,y) ∧ ¬Catches(x,y) → Frustrated(x))

Converting to CNF:
1. ¬Traffic(x) ∨ ¬Driver(y) ∨ Chases(x,y)
2. ¬Driver(x) ∨ ¬Horns(x) ∨ Smart(x)
3. ¬Traffic(x) ∨ ¬Smart(y) ∨ ¬Catches(x,y)
4. ¬Traffic(x) ∨ ¬Driver(y) ∨ ¬Chases(x,y) ∨ Catches(x,y) ∨ Frustrated(x)

Knowled

# Question 2: Pugu, Anmol and Heroes

**Problem**:
- Anyone whom Pugu loves is a star
- Any hero who does not rehearse does not act
- Anmol is a hero
- Any hero who does not work does not rehearse
- Anyone who does not act is not a star

**Goal**: Prove "If Anmol does not work, then Pugu does not love Anmol"

In [12]:
print("=== Question 2: Pugu, Anmol and Heroes ===")
print()
print("Given facts:")
print("1. Anyone whom Pugu loves is a star")
print("2. Any hero who does not rehearse does not act")
print("3. Anmol is a hero")
print("4. Any hero who does not work does not rehearse")
print("5. Anyone who does not act is not a star")
print()
print("Goal: If Anmol does not work, then Pugu does not love Anmol")
print()

print("Converting to First-Order Predicate Logic:")
print("Predicates:")
print("  Loves(p,x) - Pugu loves x")
print("  Star(x) - x is a star")
print("  Hero(x) - x is a hero")
print("  Rehearses(x) - x rehearses")
print("  Acts(x) - x acts")
print("  Works(x) - x works")
print("Constants: Pugu, Anmol")
print()

print("FOPL statements:")
print("1. ∀x (Loves(Pugu,x) → Star(x))")
print("2. ∀x (Hero(x) ∧ ¬Rehearses(x) → ¬Acts(x))")
print("3. Hero(Anmol)")
print("4. ∀x (Hero(x) ∧ ¬Works(x) → ¬Rehearses(x))")
print("5. ∀x (¬Acts(x) → ¬Star(x))")
print()

print("Converting to CNF:")
print("1. ¬Loves(Pugu,x) ∨ Star(x)")
print("2. ¬Hero(x) ∨ Rehearses(x) ∨ ¬Acts(x)")
print("3. Hero(Anmol)")
print("4. ¬Hero(x) ∨ Works(x) ∨ ¬Rehearses(x)")
print("5. Acts(x) ∨ ¬Star(x)")
print()

# Create constants and variables
x = Variable('x')
pugu = Constant('Pugu')
anmol = Constant('Anmol')

# Create clauses
clauses = [
    # 1. ¬Loves(Pugu,x) ∨ Star(x)
    FOLClause([Predicate('Loves', [pugu, x]).negate(), Predicate('Star', [x])]),
    
    # 2. ¬Hero(x) ∨ Rehearses(x) ∨ ¬Acts(x)
    FOLClause([Predicate('Hero', [x]).negate(), Predicate('Rehearses', [x]), Predicate('Acts', [x]).negate()]),
    
    # 3. Hero(Anmol)
    FOLClause([Predicate('Hero', [anmol])]),
    
    # 4. ¬Hero(x) ∨ Works(x) ∨ ¬Rehearses(x)
    FOLClause([Predicate('Hero', [x]).negate(), Predicate('Works', [x]), Predicate('Rehearses', [x]).negate()]),
    
    # 5. Acts(x) ∨ ¬Star(x)
    FOLClause([Predicate('Acts', [x]), Predicate('Star', [x]).negate()]),
]

# Add assumption: Anmol does not work
clauses.append(FOLClause([Predicate('Works', [anmol]).negate()]))

# Add negation of conclusion: Pugu loves Anmol
clauses.append(FOLClause([Predicate('Loves', [pugu, anmol])]))

print("Knowledge base with assumption and negated conclusion:")
for i, clause in enumerate(clauses):
    print(f"  {i+1}. {clause}")
print()

# Apply resolution
result, steps = fol_resolution(clauses)

print("Resolution Process:")
for step in steps:
    print(step)

print(f"\n✓ Conclusion: The statement is {'PROVABLE' if result else 'NOT provable'}")
if result:
    print("Therefore: If Anmol does not work, then Pugu does not love Anmol.")

=== Question 2: Pugu, Anmol and Heroes ===

Given facts:
1. Anyone whom Pugu loves is a star
2. Any hero who does not rehearse does not act
3. Anmol is a hero
4. Any hero who does not work does not rehearse
5. Anyone who does not act is not a star

Goal: If Anmol does not work, then Pugu does not love Anmol

Converting to First-Order Predicate Logic:
Predicates:
  Loves(p,x) - Pugu loves x
  Star(x) - x is a star
  Hero(x) - x is a hero
  Rehearses(x) - x rehearses
  Acts(x) - x acts
  Works(x) - x works
Constants: Pugu, Anmol

FOPL statements:
1. ∀x (Loves(Pugu,x) → Star(x))
2. ∀x (Hero(x) ∧ ¬Rehearses(x) → ¬Acts(x))
3. Hero(Anmol)
4. ∀x (Hero(x) ∧ ¬Works(x) → ¬Rehearses(x))
5. ∀x (¬Acts(x) → ¬Star(x))

Converting to CNF:
1. ¬Loves(Pugu,x) ∨ Star(x)
2. ¬Hero(x) ∨ Rehearses(x) ∨ ¬Acts(x)
3. Hero(Anmol)
4. ¬Hero(x) ∨ Works(x) ∨ ¬Rehearses(x)
5. Acts(x) ∨ ¬Star(x)

Knowledge base with assumption and negated conclusion:
  1. ¬Loves(Pugu, x) ∨ Star(x)
  2. ¬Hero(x) ∨ Rehearses(x) ∨ ¬Acts(x

# Question 3: Students and Intelligence

**Problem**:
- All students of BSC CSIT are intelligent person
- All friends of intelligent person are smart
- Laxmi is a friend of Rojina
- Rojina is smart
- All beautiful students are girl
- Laxmi is beautiful

**Goal**: Prove "Laxmi is smart"

In [13]:
print("=== Question 3: Students and Intelligence ===")
print()
print("Given facts:")
print("1. All students of BSC CSIT are intelligent person")
print("2. All friends of intelligent person are smart")
print("3. Laxmi is a friend of Rojina")
print("4. Rojina is smart")
print("5. All beautiful students are girl")
print("6. Laxmi is beautiful")
print()
print("Goal: Laxmi is smart")
print()

print("Converting to First-Order Predicate Logic:")
print("Predicates:")
print("  Student_BSCCSIT(x) - x is a BSC CSIT student")
print("  Intelligent(x) - x is intelligent")
print("  Friend(x,y) - x is a friend of y")
print("  Smart(x) - x is smart")
print("  Beautiful(x) - x is beautiful")
print("  Girl(x) - x is a girl")
print("Constants: Laxmi, Rojina")
print()

print("FOPL statements:")
print("1. ∀x (Student_BSCCSIT(x) → Intelligent(x))")
print("2. ∀x∀y (Friend(x,y) ∧ Intelligent(y) → Smart(x))")
print("3. Friend(Laxmi, Rojina)")
print("4. Smart(Rojina)")
print("5. ∀x (Beautiful(x) ∧ Student_BSCCSIT(x) → Girl(x))")
print("6. Beautiful(Laxmi)")
print()

print("Converting to CNF:")
print("1. ¬Student_BSCCSIT(x) ∨ Intelligent(x)")
print("2. ¬Friend(x,y) ∨ ¬Intelligent(y) ∨ Smart(x)")
print("3. Friend(Laxmi, Rojina)")
print("4. Smart(Rojina)")
print("5. ¬Beautiful(x) ∨ ¬Student_BSCCSIT(x) ∨ Girl(x)")
print("6. Beautiful(Laxmi)")
print()

# Create constants and variables
x, y = Variable('x'), Variable('y')
laxmi = Constant('Laxmi')
rojina = Constant('Rojina')

# Create clauses
clauses = [
    # 1. ¬Student_BSCCSIT(x) ∨ Intelligent(x)
    FOLClause([Predicate('Student_BSCCSIT', [x]).negate(), Predicate('Intelligent', [x])]),
    
    # 2. ¬Friend(x,y) ∨ ¬Intelligent(y) ∨ Smart(x)
    FOLClause([Predicate('Friend', [x, y]).negate(), Predicate('Intelligent', [y]).negate(), Predicate('Smart', [x])]),
    
    # 3. Friend(Laxmi, Rojina)
    FOLClause([Predicate('Friend', [laxmi, rojina])]),
    
    # 4. Smart(Rojina)
    FOLClause([Predicate('Smart', [rojina])]),
    
    # 5. ¬Beautiful(x) ∨ ¬Student_BSCCSIT(x) ∨ Girl(x)
    FOLClause([Predicate('Beautiful', [x]).negate(), Predicate('Student_BSCCSIT', [x]).negate(), Predicate('Girl', [x])]),
    
    # 6. Beautiful(Laxmi)
    FOLClause([Predicate('Beautiful', [laxmi])]),
]

# Add negation of conclusion: ¬Smart(Laxmi)
clauses.append(FOLClause([Predicate('Smart', [laxmi]).negate()]))

print("Knowledge base with negated conclusion:")
for i, clause in enumerate(clauses):
    print(f"  {i+1}. {clause}")
print()

# Let's trace through the logical reasoning manually first
print("Manual reasoning:")
print("From facts 3 and 4: Friend(Laxmi, Rojina) and Smart(Rojina)")
print("From Smart(Rojina), we need to find if Rojina is Intelligent to use fact 2")
print("Let's assume Rojina is a BSC CSIT student, then from fact 1: Intelligent(Rojina)")
print("From fact 2 with Friend(Laxmi, Rojina) and Intelligent(Rojina): Smart(Laxmi)")
print()

# Add assumption that Rojina is a BSC CSIT student
clauses.insert(-1, FOLClause([Predicate('Student_BSCCSIT', [rojina])]))

print("Updated knowledge base (assuming Rojina is a BSC CSIT student):")
for i, clause in enumerate(clauses):
    print(f"  {i+1}. {clause}")
print()

# Apply resolution
result, steps = fol_resolution(clauses)

print("Resolution Process:")
for step in steps:
    print(step)

print(f"\n✓ Conclusion: 'Laxmi is smart' is {'PROVABLE' if result else 'NOT provable'}")
if result:
    print("Therefore: Laxmi is smart.")
else:
    print("Note: We need additional information about Rojina being intelligent to prove this.")

=== Question 3: Students and Intelligence ===

Given facts:
1. All students of BSC CSIT are intelligent person
2. All friends of intelligent person are smart
3. Laxmi is a friend of Rojina
4. Rojina is smart
5. All beautiful students are girl
6. Laxmi is beautiful

Goal: Laxmi is smart

Converting to First-Order Predicate Logic:
Predicates:
  Student_BSCCSIT(x) - x is a BSC CSIT student
  Intelligent(x) - x is intelligent
  Friend(x,y) - x is a friend of y
  Smart(x) - x is smart
  Beautiful(x) - x is beautiful
  Girl(x) - x is a girl
Constants: Laxmi, Rojina

FOPL statements:
1. ∀x (Student_BSCCSIT(x) → Intelligent(x))
2. ∀x∀y (Friend(x,y) ∧ Intelligent(y) → Smart(x))
3. Friend(Laxmi, Rojina)
4. Smart(Rojina)
5. ∀x (Beautiful(x) ∧ Student_BSCCSIT(x) → Girl(x))
6. Beautiful(Laxmi)

Converting to CNF:
1. ¬Student_BSCCSIT(x) ∨ Intelligent(x)
2. ¬Friend(x,y) ∨ ¬Intelligent(y) ∨ Smart(x)
3. Friend(Laxmi, Rojina)
4. Smart(Rojina)
5. ¬Beautiful(x) ∨ ¬Student_BSCCSIT(x) ∨ Girl(x)
6. Beautiful